# Pontfelhők és robotok

Az autonóm robotok irányításához ismernünk kell környezetüket, ami a legpontosabban egy pontfelhő felvételével történhet. Ezek készítésének számos módja lehetséges, a nagyon költséges lidar-októl egészen az néhány 10 000 forintos játékra fejleszett eszközökig (Kinect). 
A felvétel módjától függetlenül nagy előnye ezeknek az adatforrásoknak, hogy 3 dimenziós képet adnak a környezetről, ami alapján jóval könnyebben lehet döntést hozni, hogy az adott térrész bejárható-e. 

Erről egy látványos videó:
[![IMAGE ALT TEXT HERE](http://img.youtube.com/vi/262S-Z1o4tw/1.jpg)](https://www.youtube.com/watch?v=262S-Z1o4tw&t=0s)

Ebben a háziban a feladat az lesz, hogy egy pontfelhőn találjuk meg a földet és ez alapján jelöljük be a számunka nem bejárható területeket. Lehet többen már láttátok az alsó videót, mi a sarokban mutatott kis ábra egyszerűsített változatát szeretnénk majd a házitok eredményeként kapni: 

[![IMAGE ALT TEXT HERE](http://img.youtube.com/vi/Ve9kWX_KXus/1.jpg)](https://www.youtube.com/watch?v=Ve9kWX_KXus&t=60s)


## Adatok beolvasása 


Első körben olvassuk be az adatokat, amiket egy Kinect V2-vel készítettünk. Első lépésben át kell alakítanunk a beolvasott mélységi képet pontfelfővé az Open3D segítségével. 

In [3]:
# Trükkös telepítés verzióval
! pip install open3d==0.12.0

In [5]:
import open3d as o3d
import numpy as np

# A kamera ismerete elengedheteten a 3D felhősítéshez 
pinhole_camera_intrinsic = o3d.camera.PinholeCameraIntrinsic(
            o3d.camera.PinholeCameraIntrinsicParameters.Kinect2DepthCameraDefault)
print(pinhole_camera_intrinsic.intrinsic_matrix)

# egy a KTK folyósóján készített kép olvasása 
color_data = o3d.io.read_image("melyseg_folyoso_szinezett.png")
# a mélységi adatok
depth_data = o3d.io.read_image("melyseg_folyoso.png")
rgbd_image = o3d.geometry.RGBDImage.create_from_color_and_depth(
        color_data, depth_data)

pcd = o3d.geometry.PointCloud.create_from_rgbd_image(
        rgbd_image, pinhole_camera_intrinsic)

o3d.visualization.draw_geometries([pcd.paint_uniform_color([0.3, 0.3, 0.3])]) 

[[365.456   0.    254.878]
 [  0.    365.456 205.395]
 [  0.      0.      1.   ]]


Ha jobban meg szeretnénk vizsgálni a pontokat és a nyers adatokkal is szeretnénk dolgozni, akkor érdemes átrakni az adatokat más formátumba. Ezt a **pcd.points** paranccsal tehetjük meg. Mivel 160512 pontja van ennek a felhőnek, ezért érdemes csak minden 10.-et megjeleníteni, ezzel könnyítve a gépünk dologát. A saját dolgunkat azzal könnyíthetjük, ha az adatokat berakjuk egy dataframe-be, mert akkor könnyen megjeleníthetjük a dolgunkat a plotly-s megjelenítésnél.

In [6]:
pcd.points

std::vector<Eigen::Vector3d> with 160512 elements.
Use numpy.asarray() to access data.

In [7]:
import pandas as pd
import plotly.express as px
from plotly.offline import init_notebook_mode
init_notebook_mode(connected=True)

# könnyebb kezelhetőség miatt dataframe készítése az adatokból.
df = pd.DataFrame(np.asarray(pcd.points)[::10], columns = ["x","y","z"])

# megjelenítés - szín a magasság alapján 
fig = px.scatter_3d(df, x='x', y='y', z='z',
              color='z')
fig.show()

Így már jobban látható az akadály, amit a robot elé raktam. Azt tudjuk még, hogy a robot előtt közvetlenül a síknak tekinthető padló van. 

# Feladat 1. 

Határozzuk meg a padló síkjának egyenletét! (Segítségképp megadtam a tartományt, ahol illeszthetünk tetszőleges módon síkot.)

In [8]:
# mostmár nem szeretnék adatot eldobni
df_nagy = pd.DataFrame(np.asarray(pcd.points), columns = ["x","y","z"])
# egyszerű szűrése a területnek -0.6<x<0.3 és 0.3<y<0.5 esetén
df_robot_elotti_sik = df_nagy.iloc[(df_nagy.x.values>-0.6)*(df_nagy.x.values<0.3)*(df_nagy.y.values<0.5)*(df_nagy.y.values>0.3),:]

# megjelenítés
fig = px.scatter_3d(df_robot_elotti_sik, x='x', y='y', z='z',
              color='z')
fig.show()

In [1]:
# 3 kézzel kiválaszott pont alapján történt illesztés nem pontos, így kevés pontot fog érni
# helyette érdemes lehet megnézni: ransac, linear regression

### SAJÁT KÓDOD ###

Most már ismerjük a padló síkjának egyenletét, és láthatjuk, hogy nincs a megszokott "Z-up" koordinátarendszerben, ahol a z tengely jelöli a függőlegest.

## Feladat 2. 

A sík egyenlete alapján forgassuk meg a pontfelhőt, hogy a z=0 síkkal párhuzamos legyen a padló a képen!

In [9]:
# kell egy forgatásai mátrixot készíteni
# szorozzuk meg az adatokat ezzel a mátrixszal és mentsük el az adatokat egy dataframe-be, majd plotoljunk.

data = np.asarray(pcd.points)

### SAJÁT KÓDOD ###

# Feladat 3.

A robotunk nem tud mindenen áthaladni, a magasabb akadályok megakasztják. Az új, Z-UP koordinátarendszerünkben ezeket a 0.2 egységnél magasabb pontok jelölik. Színezzük be ezeket!

In [ ]:
# Pandas-ban egy új oszlop, ami akkor egy adott értékű, ha az adott akadály magasabb 0.2 egységgel, mint a síkunk.
### SAJÁT KÓDOD ###